In [1]:
import altair as alt

from ETL.EtlMask import getCountyPopulationMask

from ETL.EtlUnemployment import (
    get_unemployment_rates_from_api, 
    getUnemploymentCovidBase,
    getUnemploymentCovidCorrelationPerMonth,
    getUnemploymentRateSince122019, 
    getJuly2020UnemploymentAndMask, 
    getUnemploymentVaccineCorrelationPerMonth)
from Visualization.VizUnemployment import (
    createUnemploymentChart, 
    createUnemploymentCorrelationLineChart,
    createUnemploymentMaskChart)

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

### Load some data

In [2]:
unemployment_covid_df = getUnemploymentCovidBase()
unemployment_covid_correlation_df = getUnemploymentCovidCorrelationPerMonth(unemployment_covid_df)
unemployment_covid_df.dropna(inplace=True)
unemployment_df = getUnemploymentRateSince122019()
unemployment_freq_mask_july_df, unemployment_infreq_mask_july_df = getJuly2020UnemploymentAndMask(unemployment_covid_df)
unemployment_vaccine_df = getUnemploymentVaccineCorrelationPerMonth(df=unemployment_df)

C:\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3357: DtypeWarning: Columns (23,24,25,26) have mixed types.Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


# Has unemployment an effect on the Covid-19 response?

Stark unemployment increase was a major side effect of the Covid pandemic. 

In December 2019 (Elapsed month = 1 in the visualization below) the mean of the unemployment rate was 3.79% with an inter-quartile range (the range between the 25th and 75th percentile of 2.7% to 4.4%. 

In [3]:
unemployment_df.loc[unemployment_df["month_since_start"] == 1, "unemployment_rate"].describe()

count    3141.000000
mean        3.791913
std         1.676037
min         1.000000
25%         2.700000
50%         3.400000
75%         4.400000
max        20.900000
Name: unemployment_rate, dtype: float64

By April 2020 (Elapsed month = 4 in the visualization below) , unemployment rate had jumped to a mean of 12.38% with an inter-quartile range (the range between the 25th and 75th percentile of 8.7% of 15.5%.

Both the numbers and the visualization clearly show an increase in unemployment rate but also an in the disparities between counties as the inter-quartile distance (visualized as the width of the distribution) increased from a narrow `4.4-2.7=1.7` points to `15.5-8.7=6.8` points.

In [4]:
unemployment_df.loc[unemployment_df["month_since_start"] == 5, "unemployment_rate"].describe()

count    3141.000000
mean       12.386119
std         5.364581
min         1.900000
25%         8.700000
50%        11.700000
75%        15.500000
max        39.700000
Name: unemployment_rate, dtype: float64

In [5]:
createUnemploymentChart(unemployment_df)

alt.Chart(...)

Could unemployment rate have a bigger impact than political affiliation on the response to the Covid-19, by pushing more people to wear masks or get vaccinated, thus limiting the number of Covid-19 cases?

When we look at the *Republican* and *Democrat* counties' monthly average unemployment rate and Covid-19 cases 
(per 100k people)  since the beginning of the pandemic, we see clearly that they both follow very 
different trends. The correlation between unemployment rate and covid cases also oscillates erratically between 
low values (-0.4 and 0.4). This suggests that there is no correlation between unemployment rate and Covid-19 cases.

What we see however is that the average unemployment rate is constantly higher in *Democrat* counties than in 
*Republican* counties, while at the peak of the pandemic the average Covid-19 cases number was higher in 
*Republican* counties. however show a slightly negative correlation between unemployment and Covid-19 cases. Counties with high Coivd-19 cases are mainly counties with lower unemployment rate and counties with high unemployment rate have lower Covid-19 cases.. 

In [6]:
createUnemploymentCorrelationLineChart(
    unemployment_covid_correlation_df, 
    title="Counties Average Unemployment Rate and Covid-19 Cases Since January 2020",
    sort=["Average Covid Cases per 100k", "Average Unemployment Rate", "Correlation"]
)

alt.FacetChart(...)

If there is no correlation between unemployment rate and Covid-19 cases, could there still be one with the Covid-19 response like mask usage and vaccination?

A slightly positive correlation (0.372) between unemployment rate and *frequent* mask-wearing habits, and a slightly negative correlation (-0.371) between unemployment rate and *not frequent* mask-wearing habits seem to validate this hypothesis. 
* The higher the unemployment rate is, the more people seem to follow mask wearing guidelines.
* The lower the unemployment rate is, the more people seem __not__ to follow mask wearing guidelines.

However, more than a clear correlation, there seem to be a clearer devide along political affiliation.
* Most counties with high unemployment and high mask usage are Democrat,
* while most counties with low mask usage and low unemployment are Republican.

It seems that political affiliation is a stronger differentiator in following CDC mask-wearing guidelines than unemployment rate.

In [7]:
createUnemploymentMaskChart(unemployment_freq_mask_july_df, unemployment_infreq_mask_july_df)

alt.HConcatChart(...)

> __Encoding:__
> * As *The New York Times* mask wearing survey was conducted in July 2020, these data are compared with the counties unemployment rates in July 2020
> * '_frequently_' is calculated as the sum of the percentage of people saying they '_never_', '_rarely_' or '_sometimes_' wear a mask from The New Yoirk Times dataset
> * '_not frequently_' is calculated as the sum of the percentage of people saying they '_requently_', '_always_' wear a mask from The New Yoirk Times dataset
> * Counties with missing data have been ignored

When we look at vaccination, the above pattern seems even more clear. The correlation between the percentage of the population with at least 1 dose of vaccination and the unemployment rate is even less clear. However, as for mask-wearing behaviors, we also see that 
* the counties with high vaccination and high unemployment rates are mainly Democrat
* the counties with low vaccination and low unemployment rates are mainly Republican

As for mask-wearing, the political affiliation seems to be a stronger differentiator in following CDC vaccination guidelines than unemployment rate.

In [8]:
createUnemploymentCorrelationLineChart(
    unemployment_vaccine_df, 
    title="Counties Average Unemployment and Vaccination Rates Since January 2020",
    sort=["Average Unemployment Rate", "Average % of People with 1 Dose of Vaccine", "Correlation"]
)

alt.FacetChart(...)

> __Encoding:__
> * In this chart we use the *percentage of the population with 1 dose of vaccine* data from the CDC dataset as a *measure* of the oppeness of the population to vaccination guidelines
> * Counties with missing data have been ignored

As we wanted to verify if unemployment rate could have a stronger impact on the Covid-19 response than political affiliation, we see that 
* there is no correlation between Covid-19 case and unemployment rate, and between unemployment rate and Covid-19 response behaviors like wearing a mask or getting vaccinated 
* In average, 
  * *Democrat* counties have higher unemployment rate, less Covid cases but a better response
  * *Republican* counties have lower unemployment rate, more Covid cases but a worse response

An hypothesis - which we haven’t verified - could be that instead of unemployment rate driving a stronger response, the effect could be reverse. Counties applying lower restrictions and guidelines see the number of Covid cases increase but as businesses are not forced to close due to strict lock down measures, unemployment did not increase as much as in other counties with stricter rules.
